In [1]:
import os
import json

pathToSettings = '../../env/ai.json'
if os.path.exists(pathToSettings):
    # Load setting from Json outside of project.
    print(f'Reading settings from {pathToSettings}')
    f = open(pathToSettings)
    settingsJson = json.load(f)
    del f

    for key in settingsJson:
        os.environ[key] = settingsJson[key]
        
    del settingsJson

Reading settings from ../../env/ai.json


# Setup Web Crawler and Lookup functions

In [2]:
import requests
from bs4 import BeautifulSoup
import json
import validators 

pageCache = {}

def json_safe_loads(jsonString):
    try:
        obj = json.loads(jsonString)
    except ValueError as e:
        return None
    return obj

def remove_keys(dictionary: dict, keyList: list):
    for key in keyList:        
        if key in dictionary:
            del dictionary[key]    

def get_recipe_as_json(url: str) -> dict: 
    
    obj = json_safe_loads(url)
    if obj is not None:        
        if 'url' in obj:
            url = obj['url']
    
    url = url.replace("'", "").replace('"', '')
    
    if not validators.url(url):
        return {'error': 'Invalid url format', 'url': url }
    
    if url in pageCache:
        return pageCache[url]    

    html = requests.get(url).text   
    soup = BeautifulSoup(html)
    script = soup.find_all("script", {"id": "allrecipes-schema_1-0"})

    recipeDict = json.loads(script[0].text)[0]
    remove_keys(recipeDict, ['review', 'image', 'mainEntityOfPage', 'publisher'])
    
    pageCache[url] = recipeDict
    
    return recipeDict

# url = "https://www.allrecipes.com/recipe/212498/easy-chicken-and-broccoli-alfredo/"
# obj = get_recipe_as_json(url)
#x = get_recipe_as_json('{ "url": "https://www.allrecipes.com/recipe/235153/easy-baked-chicken-thighs/" }')
# x = get_recipe_as_json('"https://www.allrecipes.com/recipe/235153/easy-baked-chicken-thighs/"')
# print(x)

In [3]:
x = json.loads('{ "url": "https://www.allrecipes.com/recipe/235153/easy-baked-chicken-thighs/"}')
#x = json.loads('{"param1": 123}')
print(type(x))

<class 'dict'>


# Static recipe lists

In [4]:
dessertList = [
   {
      "title": "Chocolate Snack Cake",
      "url": "https://www.allrecipes.com/chocolate-snack-cake-recipe-8350343"
   },
   {
      "title": "Charred Spiced Pears with Smoky Vanilla Cherry Sauce",
      "url": "https://www.allrecipes.com/charred-spiced-pears-with-smoky-vanilla-cherry-sauce-recipe-8347080"
   },
   {
      "title": "Meringue Topped Banana Pudding",
      "url": "https://www.allrecipes.com/meringue-topped-banana-pudding-recipe-8347040"
   },
   {
      "title": "White Chocolate Cinnamon Toast Crunch Bars",
      "url": "https://www.allrecipes.com/white-chocolate-cinnamon-toast-crunch-bars-recipe-7556790"
   },
   {
      "title": "Plum Cobbler for Two",
      "url": "https://www.allrecipes.com/plum-cobbler-for-two-recipe-8304143"
   },
   {
      "title": "Pumpkin Cheesecake Cookies",
      "url": "https://www.allrecipes.com/pumpkin-cheesecake-cookies-recipe-7972485"
   },
   {
      "title": "Chocolate Whipped Cottage Cheese",
      "url": "https://www.allrecipes.com/chocolate-whipped-cottage-cheese-recipe-8303272"
   },
   {
      "title": "Nutella Ice Cream",
      "url": "https://www.allrecipes.com/nutella-ice-cream-recipe-7508716"
   },
   {
      "title": "3-Ingredient Banana Oatmeal Cookies",
      "url": "https://www.allrecipes.com/3-ingredient-banana-oatmeal-cookies-recipe-7972686"
   },
   {
      "title": "Caramel Apple Pie Cookies",
      "url": "https://www.allrecipes.com/caramel-apple-pie-cookies-recipe-7642173"
   }
]

chickenDishList = [
   {
      "title": "Crispy Roasted Chicken",
      "url": "https://www.allrecipes.com/recipe/228363/crispy-roasted-chicken/"
   },
   {
      "title": "Roasted Spatchcocked Chicken With Potatoes",
      "url": "https://www.allrecipes.com/recipe/254877/roasted-spatchcocked-chicken-with-potatoes/"
   },
   {
      "title": "Easy Baked Chicken Thighs",
      "url": "https://www.allrecipes.com/recipe/235153/easy-baked-chicken-thighs/"
   },
   {
      "title": "Crispy Baked Chicken Thighs",
      "url": "https://www.allrecipes.com/recipe/258878/crispy-baked-chicken-thighs/"
   },
   {
      "title": "Crispy and Tender Baked Chicken Thighs",
      "url": "https://www.allrecipes.com/recipe/235151/crispy-and-tender-baked-chicken-thighs/"
   },
   {
      "title": "Million Dollar Chicken",
      "url": "https://www.allrecipes.com/recipe/233953/million-dollar-chicken/"
   },
   {
      "title": "Simple Whole Roasted Chicken",
      "url": "https://www.allrecipes.com/recipe/70679/simple-whole-roasted-chicken/"
   },
   {
      "title": "Beer Can Chicken",
      "url": "https://www.allrecipes.com/recipe/214618/beer-can-chicken/"
   },
   {
      "title": "Air Fryer Chicken Thighs",
      "url": "https://www.allrecipes.com/recipe/272858/air-fryer-chicken-thighs/"
   },
   {
      "title": "Happy Roast Chicken",
      "url": "https://www.allrecipes.com/recipe/214478/happy-roast-chicken/"
   }
]

# Setup Tools

In [5]:
# Tools 
from langchain.agents import Tool


# Chicken functions
def list_chicken_recipes(query: str):     
    return chickenDishList

list_chicken_recipes_tool = Tool(name='Chicken Recipes tool', func= list_chicken_recipes, description="This tools lists the available Chicken Recipes it returns a list of recipes with a TITLE and a URL where you can fetch the recipe.")

# Dessert functions
def list_dessert_recipes(query: str):        
    return dessertList

list_dessert_recipes_tool = Tool(name='Dessert Recipes tool', func=list_dessert_recipes, 
    description="This tools lists the available Dessert Recipes it returns a list of recipes with a TITLE and a URL where you can fetch the recipe.")

# Recipe fetcher functions
def get_recipe(url: str):     
    return get_recipe_as_json(url)

get_recipe_as_json_tool = Tool(name='Get a Recipe tool', func=get_recipe, description="""
    Useful for fetching a particular recipe, you can only fetch a recipe with it's url, you must get that using another tool
    The tool uses the https://schema.org/Recipe format to store it's recipes.     
    """)

# Tool list
tools = [list_chicken_recipes_tool, list_dessert_recipes_tool, get_recipe_as_json_tool]

In [6]:
# print('Chicken dishes:')
# for i in chickenDishList:
#     print(i['title'])
    
# print('')
# print('Desserts:')
# for i in dessertList:
#     print(i['title'])

# LLM
Links


1 [tracking-inspecting-prompts-langchain-agents-weights-and-biases](https://kleiber.me/blog/2023/05/14/tracking-inspecting-prompts-langchain-agents-weights-and-biases/)

In [7]:
# from langchain.agents import load_tools
# from langchain.agents import initialize_agent
# from langchain.llms import OpenAI
# from langchain.chat_models import ChatOpenAI
# from langchain.callbacks import StdOutCallbackHandler

# from langchain.agents import initialize_agent
# llm = ChatOpenAI(temperature=0, model_name='gpt-4') # 'gpt-3.5-turbo'

# agent = initialize_agent(
#     agent="zero-shot-react-description", 
#     tools=tools, 
#     llm=llm,
#     verbose=True,
#     max_iterations=7,    
#     return_intermediate_steps=True
# )
# system = "If the answer is not in the tools or context passed to you then don't answer. \nIf you don't know the answer then say so." 
# #query = "Can you show tell me what ingredients I need for the first baked chicken recipe?"
# #query = "Can you show tell me what ingredients I need for the last baked chicken recipe? "
# #query = "What is the best baked chicken recipe? Please look across all recipes with the word 'baked' in the title" # There are 3 baked chicken recipes
# #query = "Is there a Chicken recipe that's prepared with an alchohol? And if so how long does it take in total from start time to finish?"
# #query = "Which is healthier the Caramel Apple Pie Cookies or the beer chicken? Please explain how you got to your answer."
# #query = "Is the moon closer to earth or the sun?"
# #query = "How good are the apple pie cookies?"
# query = "What tools do I need for the Nutella Ice Cream?"
# #query = "My bowl is broken, can I still make Nutella Ice Cream? Answer as a yes/no."
# #response = agent({"input": f"{system} {query}"})


In [8]:
from langchain.agents import load_tools
from langchain.agents import initialize_agent
from langchain.llms import OpenAI
from langchain.chat_models import ChatOpenAI
from langchain.load.dump import dumps

def ask_query(model, apiKey, query):
   
   if len(apiKey) > 0:
      os.environ['OPENAI_API_KEY'] = apiKey
   
   print(model)
   
   # LLM    
   llm = ChatOpenAI(temperature=0.2, model_name=model) # 'gpt-3.5-turbo'  # gpt-4
   agent = initialize_agent(agent="zero-shot-react-description", tools=tools, llm=llm, verbose=True, max_iterations=7, return_intermediate_steps=True)
   system = """
   If the answer is not in the tools or context passed to you then don't answer. \n
   If you don't know the answer then say so. \n   
   """    
   response = agent({"input": f"{system} [[RECIPENAME]] {query}"})

   # Show response    
   stepsDict = json.loads(dumps(response["intermediate_steps"], pretty=True))
   resp = 'Below are the steps the agent took to get to the Final Answer. \n"Thought" is the LLMs internal dialogue, \n"Action" is the tool it will use to fetch the next piece of information. \n"Action Input" is the input it passes the tool to fetch this information. \n"Action Response" is what was returned from the tool to the LLM at that given step. '
   resp += '\n\n'
   resp += 'Steps to solve answer using ReAct\n'
   for i in range(len(stepsDict)):
      resp += '##########################################\n'
      resp += f'Step: {i+1} of {len(stepsDict)}\n'
      resp += f"Thought: {stepsDict[i][0]['kwargs']['log']}\n"
      resp += 'Below is what the tool returned...\n'
      resp += f"Action response: {stepsDict[i][1]}\n"        
      resp += '\n'

   resp += '\nFinal Thought:\n'
   resp += response['output']
   return resp

# UI - Simple UI

In [10]:
import gradio as gr

with gr.Blocks() as demo:
    gr.Markdown("Start typing below and then click **Run** to see the output.")
    with gr.Row():
        with gr.Column():
            modelDD = gr.Dropdown(['gpt-3.5-turbo', 'gpt-4'], value='gpt-3.5-turbo')
            openAIKey = gr.Textbox(placeholder="Paste your OpenAI API Key Here", label="OpenAI API Key")    
            inp = gr.Textbox(placeholder="Type your question here...", label="Question")    
            btn = gr.Button("Run")  
            examples = ["Can you show tell me what ingredients I need for the first baked chicken recipe?",
                "I have 15 guests coming to visit, if I make the 'Chocolate Snack Cake' recipe will there be enough? ",
                "Can you show tell me what ingredients I need for the last baked chicken recipe? ",
                "What is the best baked chicken recipe? Please look across all recipes with the word 'baked' in the title", # There are 3 baked chicken recipes
                "Is there a Chicken recipe that's prepared with an alchohol? And if so how long does it take in total from start time to finish?",
                "Which is healthier the Caramel Apple Pie Cookies or the beer chicken? Please explain how you got to your answer.",
                "Is the moon closer to earth or the sun?",
                "How good are the apple pie cookies?",
                "What tools do I need for the Nutella Ice Cream?",
                "My bowl is broken, can I still make Nutella Ice Cream? Answer as a yes/no."
                ]                 
            gr.Examples(examples, [inp])
        with gr.Column():
            out = gr.TextArea(label="ReAct Answer", placeholder="The answer will go here...")
    
    btn.click(fn=ask_query, inputs=[modelDD, openAIKey, inp], outputs=out)
    
demo.launch(show_error=True)

Running on local URL:  http://127.0.0.1:7861

To create a public link, set `share=True` in `launch()`.


gpt-3.5-turbo


> Entering new AgentExecutor chain...
I need to find the first baked chicken recipe and fetch its ingredients.
Action: Chicken Recipes tool
Action Input: None
Observation: ['https://www.allrecipes.com/recipe/228363/crispy-roasted-chicken/', 'https://www.allrecipes.com/recipe/254877/roasted-spatchcocked-chicken-with-potatoes/', 'https://www.allrecipes.com/recipe/235153/easy-baked-chicken-thighs/', 'https://www.allrecipes.com/recipe/258878/crispy-baked-chicken-thighs/', 'https://www.allrecipes.com/recipe/235151/crispy-and-tender-baked-chicken-thighs/', 'https://www.allrecipes.com/recipe/233953/million-dollar-chicken/', 'https://www.allrecipes.com/recipe/70679/simple-whole-roasted-chicken/', 'https://www.allrecipes.com/recipe/214618/beer-can-chicken/', 'https://www.allrecipes.com/recipe/272858/air-fryer-chicken-thighs/', 'https://www.allrecipes.com/recipe/214478/happy-roast-chicken/']
Thought:I need to fetch the first baked chicken recipe and get its ingredients.
Action: G